# VacationPy
----

#### Note
* Keep an eye on your API usage. Use https://developers.google.com/maps/reporting/gmp-reporting as reference for how to monitor your usage and billing.

* Instructions have been included for each segment. You do not have to follow them exactly, but they are included to help you think through the steps.

In [1]:
# Dependencies and Setup
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import requests
import gmaps
import os
import json

# Import API key
from api_keys import g_key

In [2]:
gmaps.configure(api_key=g_key)

### Store Part I results into DataFrame
* Load the csv exported in Part I to a DataFrame

In [3]:
city_clean_df = pd.read_csv('city_clean.csv')
city_clean_df

Unnamed: 0               City Country        Date  Latitude  Longitude  \
0             0              kenai      US  1612387925   60.5544  -151.2583   
1             1        new norfolk      AU  1612387927  -42.7826   147.0587   
2             2            hatillo      PR  1612387928   18.4863   -66.8254   
3             3  chernoyerkovskaya      RU  1612387929   45.4331    37.7686   
4             4      leningradskiy      RU  1612387682   69.3833   178.4167   
..          ...                ...     ...         ...       ...        ...   
567         567             kasama      ZM  1612388587  -10.2129    31.1808   
568         568            colares      PT  1612388659   38.7992    -9.4469   
569         569              muhos      FI  1612388660   64.8080    25.9931   
570         570          beisfjord      NO  1612388662   68.3751    17.5988   
571         571              chara      RU  1612388663   56.9064   118.2631   

     Temperature  Humidity  Wind Speed  Cloudiness  
0          15.80        92        5.75          90  
1          59.00        89        4.00          70  
2          82.99        75        1.01          25  
3          50.00        76        4.47          85  
4         -24.56        84       11.14          65  
..           ...       ...         ...         ...  
567        61.74        97        1.03          66  
568        57.99        91        8.99          40  
569        14.00        92        8.05          90  
570        25.00        83        3.00          85  
571       -29.52        66        0.40          51  

[572 rows x 10 columns]

### Humidity Heatmap
* Configure gmaps.
* Use the Lat and Lng as locations and Humidity as the weight.
* Add Heatmap layer to map.

In [4]:
lat_lng = city_clean_df[["Latitude", "Longitude"]]
# convert to float
humidity = city_clean_df["Humidity"]
len(humidity)

572

In [6]:
%matplotlib inline

# Plot Heatmap
fig = gmaps.figure()

# Create heat layer
heat_layer = gmaps.heatmap_layer(lat_lng, weights=humidity, 
                                 dissipating=False, max_intensity=300,
                                 point_radius=1)


# Add layer
fig.add_layer(heat_layer)

# Display figure
fig

Figure(layout=FigureLayout(height='420px'))

### Create new DataFrame fitting weather criteria
* Narrow down the cities to fit weather conditions.
* Drop any rows will null values.

In [8]:
output_df = city_clean_df.loc[(city_clean_df['Temperature'] > 70)\
                                  & (city_clean_df['Temperature'] < 80)\
                                  & (city_clean_df['Wind Speed'] < 10)\
                                                   & (city_clean_df['Cloudiness'] == 0)]
output_df = output_df.dropna()
output_df

Unnamed: 0            City Country        Date  Latitude  Longitude  \
9             9  saint-philippe      RE  1612387685  -21.3585    55.7679   
146         146           wamba      NG  1612388104    8.9333     8.6000   
148         148        oussouye      SN  1612388107   12.4850   -16.5469   
329         329        cardonal      MX  1612388342   20.6000   -99.1333   
438         438    saint-joseph      RE  1612388493  -21.3667    55.6167   
440         440     komatipoort      ZA  1612388495  -25.4332    31.9548   
474         474      nelson bay      AU  1612388541  -32.7167   152.1500   
512         512            tonj      SS  1612388589    7.2737    28.6822   
553         553       ambovombe      MG  1612388640  -25.1667    46.0833   

     Temperature  Humidity  Wind Speed  Cloudiness  
9          78.80        73        2.30           0  
146        78.15        17        4.92           0  
148        78.80        78        2.30           0  
329        72.90        28        8.21           0  
438        78.80        73        3.44           0  
440        73.00        94        1.95           0  
474        75.99        78        9.22           0  
512        79.11        23        0.72           0  
553        75.43        75        7.67           0

In [9]:
hotel_df = city_clean_df.copy()
hotel_df

Unnamed: 0               City Country        Date  Latitude  Longitude  \
0             0              kenai      US  1612387925   60.5544  -151.2583   
1             1        new norfolk      AU  1612387927  -42.7826   147.0587   
2             2            hatillo      PR  1612387928   18.4863   -66.8254   
3             3  chernoyerkovskaya      RU  1612387929   45.4331    37.7686   
4             4      leningradskiy      RU  1612387682   69.3833   178.4167   
..          ...                ...     ...         ...       ...        ...   
567         567             kasama      ZM  1612388587  -10.2129    31.1808   
568         568            colares      PT  1612388659   38.7992    -9.4469   
569         569              muhos      FI  1612388660   64.8080    25.9931   
570         570          beisfjord      NO  1612388662   68.3751    17.5988   
571         571              chara      RU  1612388663   56.9064   118.2631   

     Temperature  Humidity  Wind Speed  Cloudiness  
0          15.80        92        5.75          90  
1          59.00        89        4.00          70  
2          82.99        75        1.01          25  
3          50.00        76        4.47          85  
4         -24.56        84       11.14          65  
..           ...       ...         ...         ...  
567        61.74        97        1.03          66  
568        57.99        91        8.99          40  
569        14.00        92        8.05          90  
570        25.00        83        3.00          85  
571       -29.52        66        0.40          51  

[572 rows x 10 columns]

### Hotel Map
* Store into variable named `hotel_df`.
* Add a "Hotel Name" column to the DataFrame.
* Set parameters to search for hotels with 5000 meters.
* Hit the Google Places API for each city's coordinates.
* Store the first Hotel result into the DataFrame.
* Plot markers on top of the heatmap.

In [10]:
hotel_df['Hotel Name'] = ""
hotel_df

Unnamed: 0               City Country        Date  Latitude  Longitude  \
0             0              kenai      US  1612387925   60.5544  -151.2583   
1             1        new norfolk      AU  1612387927  -42.7826   147.0587   
2             2            hatillo      PR  1612387928   18.4863   -66.8254   
3             3  chernoyerkovskaya      RU  1612387929   45.4331    37.7686   
4             4      leningradskiy      RU  1612387682   69.3833   178.4167   
..          ...                ...     ...         ...       ...        ...   
567         567             kasama      ZM  1612388587  -10.2129    31.1808   
568         568            colares      PT  1612388659   38.7992    -9.4469   
569         569              muhos      FI  1612388660   64.8080    25.9931   
570         570          beisfjord      NO  1612388662   68.3751    17.5988   
571         571              chara      RU  1612388663   56.9064   118.2631   

     Temperature  Humidity  Wind Speed  Cloudiness Hotel Name  
0          15.80        92        5.75          90             
1          59.00        89        4.00          70             
2          82.99        75        1.01          25             
3          50.00        76        4.47          85             
4         -24.56        84       11.14          65             
..           ...       ...         ...         ...        ...  
567        61.74        97        1.03          66             
568        57.99        91        8.99          40             
569        14.00        92        8.05          90             
570        25.00        83        3.00          85             
571       -29.52        66        0.40          51             

[572 rows x 11 columns]

In [ ]:
params = {
    "radius": 5000,
    "types": "Lodging",
    "keyword": "Hotel",
    "key": g_key
}

# Use the lat/lng we recovered to identify hotels
for index, row in hotel_df.iterrows():
    # get lat, lng from df
    lat = row["Latitude"]
    lng = row["Longitude"]

    # change location each iteration while leaving original params in place
    params["location"] = f"{lat},{lng}"

    # Use the search term: "International Airport" and our lat/lng
    base_url = "https://maps.googleapis.com/maps/api/place/nearbysearch/json"

    # make request and print url
    name_address = requests.get(base_url, params=params)
    
#     print the name_address url, avoid doing for public github repos in order to avoid exposing key
   # print(name_address.url)

    name_address = name_address.json()
    print(json.dumps(name_address, indent=4, sort_keys=True))

#     Since some data may be missing we incorporate a try-except to skip any that are missing a data point.
#     try:
#         cities_pd.loc[index, "Hotel Name"] = name_address["results"][0]["name"]
#     except (KeyError, IndexError):
#         print("Missing field/result... skipping.")

{
    "html_attributions": [],
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": 60.559102,
                    "lng": -151.2346845
                },
                "viewport": {
                    "northeast": {
                        "lat": 60.56082532989272,
                        "lng": -151.2317871
                    },
                    "southwest": {
                        "lat": 60.55812567010727,
                        "lng": -151.2385847
                    }
                }
            },
            "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png",
            "name": "Aspen Extended Stay Suites",
            "opening_hours": {
                "open_now": true
            },
            "photos": [
                {
                    "height": 4032,
                    "html_attributions": [
                        "<a h

{
    "html_attributions": [],
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": -42.775558,
                    "lng": 147.0766756
                },
                "viewport": {
                    "northeast": {
                        "lat": -42.77422572010728,
                        "lng": 147.0779784298927
                    },
                    "southwest": {
                        "lat": -42.77692537989272,
                        "lng": 147.0752787701072
                    }
                }
            },
            "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png",
            "name": "Tynwald Willow Bend Estate",
            "opening_hours": {
                "open_now": false
            },
            "photos": [
                {
                    "height": 1200,
                    "html_attributions": [
                

{
    "html_attributions": [],
    "results": [],
    "status": "ZERO_RESULTS"
}
{
    "html_attributions": [],
    "results": [],
    "status": "ZERO_RESULTS"
}
{
    "html_attributions": [],
    "results": [],
    "status": "ZERO_RESULTS"
}
{
    "html_attributions": [],
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": -2.0230926,
                    "lng": 147.2702419
                },
                "viewport": {
                    "northeast": {
                        "lat": -2.021811970107277,
                        "lng": 147.2715115798927
                    },
                    "southwest": {
                        "lat": -2.024511629892722,
                        "lng": 147.2688119201073
                    }
                }
            },
            "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png",
            "name": "Lor

{
    "html_attributions": [],
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": -46.2847781,
                    "lng": 169.8418844
                },
                "viewport": {
                    "northeast": {
                        "lat": -46.28348057010727,
                        "lng": 169.8432003798927
                    },
                    "southwest": {
                        "lat": -46.28618022989271,
                        "lng": 169.8405007201073
                    }
                }
            },
            "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/camping-71.png",
            "name": "Kaitangata Motor Camp",
            "opening_hours": {
                "open_now": true
            },
            "photos": [
                {
                    "height": 2322,
                    "html_attributions": [
                     

{
    "html_attributions": [],
    "next_page_token": "ATtYBwLH8de84wxdBntTcxAZQGyBN_wQ7nFpk3Sn7h6U1SERg7SbipEEHBljssd2TDUbKDnTzt7czlob3RoKyU-n38Gvkx2TZAxlrNLY_N5kDrbkYMNJPLUpau6mk6OlhWmMFSjhnM-2zXbSVA-PRuMOigCu6WAiAltfifte4WLjsIMpDIlw5o9MrvMyrokPm-6Ev5FY5QnsAoqAyKl0KUO3SiMpNPoltMZ04_u9cEoRFmGvs9J_uOxEtrKRZgZtwPgE-1i7zDAVlcT5EC1h3Ujzb8IZGr6Gwt_8Iw4vK0iJy9Y1jsUbibr2kBVHg14ykA2o88YzTirY2q_rrvVtMis_3L2QwnWO2QGJLN0SqFm_vBGdpQ4hAhIUzBpqF9kq1DeZQEAqg-CGmRXnYuriJwBOVniRJ58g1lREPi0TiaJWfQyt0YyS6i6sUg1OuqSRGPSdCQ",
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": -42.8808631,
                    "lng": 147.3335418
                },
                "viewport": {
                    "northeast": {
                        "lat": -42.87956517010728,
                        "lng": 147.3351852298927
                    },
                    "southwest": {
                        "lat": -42.882

...

{
    "html_attributions": [],
    "next_page_token": "ATtYBwKligjOJE9nFlrWgMT8uI6T5LXuLhYuucZYaizfdNztotJ4yaTwOEr-HAc7uH8Yg1kNTJpBX9SSyKAAg7wvlYueYuwhYHNz4CqMea1kiXvyeNCV34jknv9xRDddUlI06Yy8ljEbFSuj93z-yhBaeWk-gF7O5A9juSA16UVECfyH1vb1OJpn1Aq-HD6kZ0dQLbauB2ME1qm6_Iw9vX2mpWbCuh0emqBU6E_19r7T0gdLzujBtc9TwGR_m_DVUbhw37Y53vK7xnPSe-Di_M-dPna5gZnprSPUWSW34RIhZYi6lzJSQT62uF8mweLJN3iVtl4EzWXc8H7-htsyPrbLIH9YXE4dJIghXovQHlAzS781ofCpQF94XRz7GzbAXK-eebXpBgFucr5hmDDzVuioMAbEurd3eC3QkxmHit6P99zsNcIdp-5fVjMQr1McLeTfnQ",
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": 29.6127428,
                    "lng": -90.7596914
                },
                "viewport": {
                    "northeast": {
                        "lat": 29.61406757989272,
                        "lng": -90.75826267010727
                    },
                    "southwest": {
                        "lat": 29.61136

{
    "html_attributions": [],
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": 42.8450512,
                    "lng": 93.5021755
                },
                "viewport": {
                    "northeast": {
                        "lat": 42.84641312989272,
                        "lng": 93.50339707989272
                    },
                    "southwest": {
                        "lat": 42.84371347010728,
                        "lng": 93.50069742010727
                    }
                }
            },
            "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/generic_business-71.png",
            "name": "\u54c8\u5bc6\u73af\u7403\u5927\u9152\u5e97",
            "photos": [
                {
                    "height": 960,
                    "html_attributions": [
                        "<a href=\"https://maps.google.com/maps/contrib/105

{
    "html_attributions": [],
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": 69.4976485,
                    "lng": 88.3994723
                },
                "viewport": {
                    "northeast": {
                        "lat": 69.49893822989272,
                        "lng": 88.40082972989272
                    },
                    "southwest": {
                        "lat": 69.49623857010728,
                        "lng": 88.39813007010727
                    }
                }
            },
            "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png",
            "name": "Talnakh Hotel",
            "photos": [
                {
                    "height": 2988,
                    "html_attributions": [
                        "<a href=\"https://maps.google.com/maps/contrib/112896326995617295414\">Evgeny Barabanov

{
    "html_attributions": [],
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": 46.799324,
                    "lng": -92.1198806
                },
                "viewport": {
                    "northeast": {
                        "lat": 46.80069617989273,
                        "lng": -92.11904737010727
                    },
                    "southwest": {
                        "lat": 46.79799652010728,
                        "lng": -92.12174702989272
                    }
                }
            },
            "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png",
            "name": "Tru By Hilton Duluth Mall Area",
            "opening_hours": {
                "open_now": true
            },
            "photos": [
                {
                    "height": 4000,
                    "html_attributions": [
              

{
    "html_attributions": [],
    "results": [
        {
            "business_status": "OPERATIONAL",
            "geometry": {
                "location": {
                    "lat": 56.2101663,
                    "lng": 43.3820603
                },
                "viewport": {
                    "northeast": {
                        "lat": 56.21123787989272,
                        "lng": 43.38403062989272
                    },
                    "southwest": {
                        "lat": 56.20853822010727,
                        "lng": 43.38133097010728
                    }
                }
            },
            "icon": "https://maps.gstatic.com/mapfiles/place_api/icons/v1/png_71/lodging-71.png",
            "name": "Ranch 636, Country Club",
            "photos": [
                {
                    "height": 714,
                    "html_attributions": [
                        "<a href=\"https://maps.google.com/maps/contrib/102322157030535196976\">SPORT C

In [ ]:
# NOTE: Do not change any of the code in this cell

# Using the template add the hotel marks to the heatmap
info_box_template = """
<dl>
<dt>Name</dt><dd>{Hotel Name}</dd>
<dt>City</dt><dd>{City}</dd>
<dt>Country</dt><dd>{Country}</dd>
</dl>
"""

# Store the DataFrame Row
# NOTE: be sure to update with your DataFrame name
hotel_info = [info_box_template.format(**row) for index, row in hotel_df.iterrows()]
locations = hotel_df[["Lat", "Lng"]]

In [ ]:
# Add marker layer ontop of heat map
# Assign the marker layer to a variable
markers = gmaps.marker_layer(hotel_info)
markers2 = gmaps.marker_layer(locations)
# Add the layer to the map
fig.add_layer(markers)
fig.add_layer(locations)

# Display figure
fig